In [ ]:
## Optional, run to show environment and dependencies
#!conda list
#!pip freeze

# packages in environment at C:\Users\Admin\anaconda3\envs\protein_refine:
#
# Name                       Version          Build                     Channel
aiohappyeyeballs             2.6.1            pypi_0                    pypi
aiohttp                      3.12.15          pypi_0                    pypi
aiosignal                    1.4.0            pypi_0                    pypi
annotated-types              0.7.0            pypi_0                    pypi
antlr4-python3-runtime       4.9.3            pypi_0                    pypi
anyio                        4.7.0            py310haa95532_0
argon2-cffi                  21.3.0           pyhd3eb1b0_0
argon2-cffi-bindings         21.2.0           py310h827c3e9_1
asttokens                    3.0.0            py310haa95532_0
async-lru                    2.0.4            py310haa95532_0
async-timeout                5.0.1            pypi_0                    pypi
attrs                        24.3.0           py310haa95532_0
babel       

In [ ]:
#clone boltz2 repo from github and install boltz2
!git clone https://github.com/jwohlwend/boltz.git
%cd boltz
%pip install -e .[cuda]

In [ ]:
#cache will download:
#boltz2_aff.ckpt
#boltz2_conf.ckpt
#MOL_URL = "https://huggingface.co/boltz-community/boltz-2/resolve/main/mols.tar"
#The following .pkl files cannot be have their name in Windows: AUX, CON, NUL, PRN
#Workaround: In \boltz\src\boltz\data\mol.py

# change the function at line 16 to

# def load_molecules(moldir: str, molecules: list[str]) -> dict[str, Mol]:
#     loaded_mols = {}
#         for molecule in molecules:
#             path = Path(moldir) / f"{molecule}.pkl"
#             if not path.exists():
#                 # Try prepending an underscore (for reserved names like AUX)
#                 path_alt = Path(moldir) / f"_{molecule}.pkl"
#                 if path_alt.exists():
#                     path = path_alt
#                 else:
#                     msg = f"CCD component {molecule} not found! Tried {path} and {path_alt}"
#                     raise ValueError(msg)
#             with path.open("rb") as f:
#                 loaded_mols[molecule] = pickle.load(f)  # noqa: S301
#         return loaded_mols

In [46]:
#Optimizations
import torch
torch.set_float32_matmul_precision('high')

In [ ]:
# List of UniProt IDs
# uniprot_ids = [
#     'P69905',  # Hemoglobin subunit alpha (HBA_HUMAN)
#     'P02144',  # Immunoglobulin heavy constant gamma 1 (IGHG1_HUMAN)
#     'P61626',  # Cytochrome P450 2D6 (CYP2D6_HUMAN)
#     'P42212',  # Glutamate dehydrogenase 1 (GLUD1_HUMAN)
#     'P02769',  # Alpha-1-antitrypsin (SERPINA1_HUMAN)
#     'P02763',  # Alpha-2-macroglobulin (A2M_HUMAN)
#     'P02760',  # Complement C3 (C3_HUMAN)
#     'P02748',  # Apolipoprotein B-100 (APOB_HUMAN)
#     'P02747',  # Apolipoprotein C-I (APOC1_HUMAN)
#     'P02750',  # Apolipoprotein C-III (APOC3_HUMAN)
#     'P02752',  # Apolipoprotein E (APOE_HUMAN)
#     'P02753',  # Apolipoprotein F (APOF_HUMAN)
#     'P02754',  # Apolipoprotein H (APOH_HUMAN)
#     'P09466',#  Human Glycodelin
#     'P02754',#  Bovine Beta-lactoglobulin B variant
#     'P02649',#  Human Albumin (well-structured, large)
#     'P03973',#  Canine Serum Albumin (another albumin family)
#     'P31725',#  Human AKT1 (kinase domain, good structure)
#     'P00734' #  Human Complement C3 (immune-related)
#     'P01033' # Alpha-1-antichymotrypsin (SERPINA3)
# ]

uniprot_ids=[
    
]


#Unavailable IDs: P02757 P02756 P02755 P02749 P02766 P02751 P02742

# Protein Families Represented:
# Hemoglobin: Oxygen transport
# Immunoglobulins: Immune response
# Cytochrome P450: Drug metabolism
# Dehydrogenases: Metabolic enzymes
# Serpins: Protease inhibitors
# Complement proteins: Immune system
# Apolipoproteins: Lipid transport

# Why This Set?
# Diversity: Covers various protein types and functions.
# Structural Variety: Includes globular, fibrous, and membrane-associated proteins.
# Relevance: Proteins like hemoglobin and immunoglobulins are well-studied, providing benchmarks for accuracy.

# Params

boltz_params = {
    "model_name": "boltz2",
    "devices": 1,
    "accelerator": "gpu",
    "use_potentials": True,
    "num_workers": 8,
    "step_scale": 1.638,
    "diffusion_samples": 1,
    "recycling_steps": 3,
    "sampling_steps": 50,
    "output_format": "pdb"
}

esm_model_name="esm2_t33_650M_UR50D"

functional_percentile=80
flexible_percentile=80

move_factor=0.1

In [2]:
#Set directories

import os

work_dir = os.path.dirname(os.path.abspath(__file__)) if "__file__" in globals() else os.getcwd()
boltz_cache_dir = os.path.join(work_dir, "boltz", "boltz_cache")
boltz_out_dir = os.path.join(work_dir, "boltz_predictions")
yaml_dir = os.path.join(work_dir, "yamls")
refine_out_dir = os.path.join(work_dir, "refined_results")

print("Working directory:", work_dir)
print("Boltz Cache directory:", boltz_cache_dir)
print("Boltz Output directory:", boltz_out_dir)
print("YAML directory:", yaml_dir)
print("Refine Output directory:", refine_out_dir)

# Tell Boltz to use this cache
os.environ["BOLTZ_CACHE"] = boltz_cache_dir


Working directory: c:\School\URECA\Code\RefinementExperiment
Boltz Cache directory: c:\School\URECA\Code\RefinementExperiment\boltz\boltz_cache
Boltz Output directory: c:\School\URECA\Code\RefinementExperiment\boltz_predictions
YAML directory: c:\School\URECA\Code\RefinementExperiment\yamls
Refine Output directory: c:\School\URECA\Code\RefinementExperiment\refined_results


In [3]:
import requests
import string

# UniProt fetcher
def fetch_uniprot_sequence(uid):
    """Fetch sequence and protein name from UniProt."""
    url = f"https://rest.uniprot.org/uniprotkb/{uid}.fasta"
    response = requests.get(url)
    if response.status_code == 200:
        lines = response.text.splitlines()
        header = lines[0][1:].strip()
        sequence = ''.join(lines[1:]).upper().replace(" ", "").replace("\n", "")
        #molecule_name = header.split(" ", 1)[1] if " " in header else uid #set molecule_name to its name in UniProt (may cause filesystem issues)
        #molecule_name = molecule_name.replace(" ", "_")
        molecule_name = uid # Use only the UniProt ID to avoid filesystem issues
        return sequence, molecule_name
    else:
        print(f"Failed to fetch data for {uid}")
        return None, None

# YAML generators
def make_yaml_single(uid, sequence, molecule_name):
    """Generate a single YAML file for one protein."""
    yaml_content = f"""
version: 1
sequences:
  - protein:
      id: [A]
      sequence: {sequence}
      msa: empty
"""
    yaml_path = os.path.join(yaml_dir, f"{molecule_name}.yaml")
    with open(yaml_path, "w") as f:
        f.write(yaml_content.strip() + "\n")
    print(f"Single YAML created: {yaml_path}")
    return yaml_path

def make_yaml_combined(uniprot_data, combined_name="combined_proteins"):
    """Generate one YAML with multiple proteins, assigning chain IDs A, B, C..."""
    chain_ids = string.ascii_uppercase
    yaml_lines = ["version: 1", "sequences:"]
    for i, (uid, seq, name) in enumerate(uniprot_data):
        yaml_lines.append(f"  - protein:")
        yaml_lines.append(f"      id: [{chain_ids[i]}]")
        yaml_lines.append(f"      sequence: {seq}")
        yaml_lines.append(f"      msa: empty")
    yaml_content = "\n".join(yaml_lines)
    yaml_path = os.path.join(yaml_dir, f"{combined_name}.yaml")
    with open(yaml_path, "w") as f:
        f.write(yaml_content + "\n")
    print(f"Combined YAML created: {yaml_path}")
    return yaml_path

# Optional: create one combined YAML
#make_yaml_combined(uniprot_data, combined_name="all_proteins")


In [11]:
#Run Boltz2 prediction
def run_boltz_predict(yaml_path, out_dir, cache_dir, params):
    print(f"Running Boltz2 prediction -> {out_dir}")
    !boltz predict {yaml_path} \
        --out_dir {out_dir} \
        --model {params['model_name']} \
        --devices {params['devices']} \
        --accelerator {params['accelerator']} \
        {"--use_potentials" if params['use_potentials'] else ""} \
        --num_workers {params['num_workers']} \
        --step_scale {params['step_scale']} \
        --diffusion_samples {params['diffusion_samples']} \
        --recycling_steps {params['recycling_steps']} \
        --sampling_steps {params['sampling_steps']} \
        --output_format {params['output_format']} \
        --cache {cache_dir}
    print(f"Boltz2 prediction complete: {out_dir}")

    import os

def get_boltz_output_pdb(molecule_name):
    """
    Returns the path to the Boltz2 predicted PDB for a given molecule name.
    """
    pdb_path = os.path.join(
        boltz_out_dir,
        f"boltz_results_{molecule_name}",
        "predictions",
        f"{molecule_name}",
        f"{molecule_name}_model_0.pdb"
    )
    if not os.path.exists(pdb_path):
        raise FileNotFoundError(f"Boltz2 output PDB not found: {pdb_path}")
    return pdb_path

def check_boltz_output_pdb(molecule_name):
    """
    Check if the Boltz2 predicted PDB exists for a given molecule name.
    Returns True if exists, False otherwise.
    """
    pdb_path = os.path.join(
        boltz_out_dir,
        f"boltz_results_{molecule_name}",
        "predictions",
        f"{molecule_name}",
        f"{molecule_name}_model_0.pdb"
    )
    return os.path.exists(pdb_path)



In [5]:
from Bio.PDB import PDBParser

def pdb_to_sequence(pdb_file):
    """
    Extract amino acid sequence from a PDB file.
    
    Args:
        pdb_file (str): Path to a PDB file
    
    Returns:
        sequence (str): Amino acid sequence
    """
    aa_dict = {
        'ALA': 'A', 'CYS': 'C', 'ASP': 'D', 'GLU': 'E', 'PHE': 'F',
        'GLY': 'G', 'HIS': 'H', 'ILE': 'I', 'LYS': 'K', 'LEU': 'L',
        'MET': 'M', 'ASN': 'N', 'PRO': 'P', 'GLN': 'Q', 'ARG': 'R',
        'SER': 'S', 'THR': 'T', 'VAL': 'V', 'TRP': 'W', 'TYR': 'Y'
    }

    parser = PDBParser(QUIET=True)
    structure = parser.get_structure("model", pdb_file)
    model = structure[0]
    sequence = ""
    for chain in model:
        for residue in chain:
            # Ignore heteroatoms and non-standard residues
            if residue.get_id()[0] == " ":
                resname = residue.get_resname()
                sequence += aa_dict.get(resname, "")
    if not sequence:
        raise ValueError(f"No valid residues found in PDB: {pdb_file}")
    return sequence


In [6]:
import esm
import torch
import numpy as np

#Functional Anchors: Residues predicted to be structurally or functionally important (active sites, binding sites, or residues that stabilize the structure)
# For each residue, we compute an embedding from the ESM2 model. This is a high-dimensional vector representing the residue in the context of the whole protein.
# We take the L2 norm (magnitude) of this embedding. Intuitively, residues with higher norms carry more unique or significant structural information.
# We set a percentile threshold (e.g., 80th percentile) to pick the top residues. Only residues whose L2 norm is above this threshold are labeled as functional anchors

#Flexible Anchors (Flexible Regions): Residues predicted to be more dynamic or flexible. These regions can move more freely and are less likely to be part of rigid functional cores. They can be useful to allow “small adjustments” during structural refinement
# # We compute attention entropy from the ESM2 model.
# Attention entropy measures how spread-out the attention is for a residue across the sequence.
# Low entropy → residue attends strongly to only a few residues → usually structurally important.
# High entropy → residue attends to many residues → potentially flexible.
# We pick residues with attention entropy above a certain percentile (e.g., 80th percentile) as flexible anchors.

#Percentile: cutoff threshold to separate “important” residues from the rest
#Functional percentile = 80 : top 20% of residues by embedding magnitude are considered functional anchors


def predict_anchors_from_boltz2(
    pdb_file,
    model,
    batch_converter,
    functional_percentile=80, #default 80th percentile
    flexible_percentile=80
):
    """
    Predict functional and flexible anchor residues from a Boltz2 PDB structure,
    using a preloaded ESM2 model and batch converter.
    """
    # Extract sequence
    sequence = pdb_to_sequence(pdb_file)
    print(f"Extracted sequence from PDB (length={len(sequence)})")

    # Prepare sequence batch
    data = [("protein", sequence)]
    _, _, batch_tokens = batch_converter(data)

    # Generate embeddings and attention
    with torch.no_grad():
        results = model(batch_tokens, repr_layers=[12], return_contacts=True)
        embeddings = results["representations"][12][0, 1:-1]
        attention_weights = results["attentions"][0]

    # Compute residue importance and attention entropy
    importance = torch.norm(embeddings, dim=1).cpu().numpy()
    avg_attention = attention_weights.mean(dim=(0, 1))
    seq_len = len(sequence)
    attention_len = min(avg_attention.shape[0], seq_len)
    
    attention_entropy = []
    for i in range(attention_len):
        attn = avg_attention[i]
        entropy = -torch.sum(attn * torch.log(attn + 1e-8)).item()
        attention_entropy.append(entropy)
    attention_entropy = np.array(attention_entropy)

    # Trim to same length
    min_len = min(len(importance), len(attention_entropy))
    importance = importance[:min_len]
    attention_entropy = attention_entropy[:min_len]

    # Identify functional and flexible sites
    importance_threshold = np.percentile(importance, functional_percentile)
    entropy_threshold = np.percentile(attention_entropy, 100 - functional_percentile)
    flexible_threshold = np.percentile(attention_entropy, flexible_percentile)

    functional_sites = [i + 1 for i, (imp, ent) in enumerate(zip(importance, attention_entropy))
                        if imp > importance_threshold and ent < entropy_threshold]
    flexible_sites = [i + 1 for i, ent in enumerate(attention_entropy) if ent > flexible_threshold]

    # Map to sequence residues
    functional_anchors = [(i, sequence[i - 1]) for i in functional_sites]
    flexible_anchors = [(i, sequence[i - 1]) for i in flexible_sites]

    print(f"Predicted {len(functional_anchors)} functional anchors and {len(flexible_anchors)} flexible regions")
    return functional_anchors, flexible_anchors


In [7]:
#Structure refinement

from Bio.PDB import PDBParser, PDBIO, is_aa
from pathlib import Path

# Helper functions

def load_structure_coords(pdb_path):
    """Load CA coordinates from a PDB structure"""
    parser = PDBParser(QUIET=True)
    structure = parser.get_structure("prot", pdb_path)
    coords = {}
    for chain in structure[0]:
        for res in chain:
            if is_aa(res) and 'CA' in res:
                coords[res.id[1]] = res['CA'].get_coord()
    return structure, coords

def apply_constraints(coords, fixed_residues, move_factor=0.1): #default move factor=0.1
    """
    Move all residues slightly toward the mean of fixed residues (functional anchors)
    Fixed residues remain in place
    """
    fixed_coords = np.array([coords[r] for r in fixed_residues if r in coords])
    if len(fixed_coords) == 0:
        print("Warning: No fixed residues found in coordinates!")
        return coords
    mean_fixed = fixed_coords.mean(axis=0)

    new_coords = {}
    for res_id, coord in coords.items():
        if res_id in fixed_residues:
            new_coords[res_id] = coord
        else:
            direction = mean_fixed - coord
            new_coords[res_id] = coord + move_factor * direction
    return new_coords

def save_refined_structure(structure, new_coords, out_pdb):
    """Save structure with updated CA coordinates"""
    for chain in structure[0]:
        for res in chain:
            res_id = res.id[1]
            if res_id in new_coords and 'CA' in res:
                res['CA'].set_coord(new_coords[res_id])
    io = PDBIO()
    io.set_structure(structure)
    io.save(out_pdb)


# Main refinement function

def refine_with_esm(pred_pdb, esm_annotations, out_dir="./refined_results", move_factor=0.2):
    """
    Refine a Boltz2 PDB using ESM2 annotations.
    
    pred_pdb: path to Boltz2 output PDB
    esm_annotations: dict with keys "functional_sites" and optional "flexible_sites"
    out_dir: folder to save refined PDB
    """
    Path(out_dir).mkdir(exist_ok=True, parents=True)

    # Extract sites from ESM2 annotations
    functional_sites = esm_annotations.get("functional_sites", [])
    flexible_sites = esm_annotations.get("flexible_sites", [])

    fixed_residues = functional_sites  # keep functional anchors fixed

    # Load and adjust coords
    structure, coords = load_structure_coords(pred_pdb)
    new_coords = apply_constraints(coords, fixed_residues, move_factor=move_factor)

    # Save new pdb
    name = Path(pred_pdb).stem
    refined_pdb_path = f"{out_dir}/{name}_refined.pdb"
    save_refined_structure(structure, new_coords, refined_pdb_path)

    return refined_pdb_path




In [8]:
#Fetch ground truth and calculate rmsd

from Bio.PDB import PDBParser, MMCIFParser, Superimposer, is_aa

ground_truth_dir = "./ground_truth"
os.makedirs(ground_truth_dir, exist_ok=True)

def download_pdb_from_uniprot(uniprot_id):
    """
    Download the first available PDB structure for a UniProt ID.
    Returns the path to the downloaded PDB file or None.
    """
    url_mapping = f"https://www.uniprot.org/uniprot/{uniprot_id}.xml"
    resp = requests.get(url_mapping)
    if resp.status_code != 200:
        print(f"Failed to get UniProt XML for {uniprot_id}")
        return None

    # Parse XML to get the first PDB entry
    import xml.etree.ElementTree as ET
    root = ET.fromstring(resp.text)
    ns = {"ns": "http://uniprot.org/uniprot"}
    pdb_refs = root.findall(".//ns:dbReference[@type='PDB']", ns)
    if not pdb_refs:
        print(f"No PDB entry found for {uniprot_id}")
        return None
    pdb_id = pdb_refs[0].attrib["id"].lower()

    # Download PDB file from RCSB
    pdb_file_path = os.path.join(ground_truth_dir, f"{uniprot_id}_{pdb_id}.pdb")
    pdb_url = f"https://files.rcsb.org/download/{pdb_id.upper()}.pdb"
    resp = requests.get(pdb_url)
    if resp.status_code == 200:
        with open(pdb_file_path, "w") as f:
            f.write(resp.text)
        print(f"Downloaded PDB for {uniprot_id}: {pdb_file_path}")
        return pdb_file_path
    else:
        print(f"Failed to download PDB {pdb_id}")
        return None

def calc_rmsd(pred_pdb, ref_pdb):
    """
    Compute RMSD between predicted and reference PDB structures based on CA atoms.
    """
    parser = PDBParser(QUIET=True)
    pred_struct = parser.get_structure("pred", pred_pdb)
    ref_struct = parser.get_structure("ref", ref_pdb)

    pred_atoms = [res["CA"] for chain in pred_struct[0] for res in chain if is_aa(res) and "CA" in res]
    ref_atoms = [res["CA"] for chain in ref_struct[0] for res in chain if is_aa(res) and "CA" in res]

    n = min(len(pred_atoms), len(ref_atoms))
    if n == 0:
        print(f"No CA atoms to compare between {pred_pdb} and {ref_pdb}")
        return None

    sup = Superimposer()
    sup.set_atoms(ref_atoms[:n], pred_atoms[:n])
    return sup.rms


In [15]:
#  Main loop 
import pandas as pd

torch.set_float32_matmul_precision('high')

print(f"Loading ESM model: {esm_model_name}")
model, alphabet = getattr(esm.pretrained, esm_model_name)()
batch_converter = alphabet.get_batch_converter()
model.eval()

# Prepare output CSV
# if not rmsd_results:
#     rmsd_results = []

rmsd_results = []

for uid in uniprot_ids:
    print(f"Attempting to fetch {uid}")
    sequence, molecule_name = fetch_uniprot_sequence(uid)
    if not sequence:
        print(f"Skipping {uid} due to missing sequence")
        continue
    if sequence:
        # Generate YAML and run Boltz2
        yaml_path = make_yaml_single(uid, sequence, molecule_name)
        #run_boltz_predict(yaml_path, boltz_out_dir, boltz_cache_dir, boltz_params)
        
        

        boltz_output_already = check_boltz_output_pdb(molecule_name)
        if boltz_output_already:
            print(f"Found Boltz2 output PDB for {uid}, skipping Boltz2 prediction")

        else:
            print(f"Running Boltz2 prediction for {uid} ({uniprot_ids.index(uid)+1}/{len(uniprot_ids)})")
            !boltz predict {yaml_path} \
            --out_dir {boltz_out_dir} \
            --model "{boltz_params['model_name']}" \
            --devices "{boltz_params['devices']}" \
            --accelerator "{boltz_params['accelerator']}" \
            {"--use_potentials" if boltz_params['use_potentials'] else ""}  \
            --num_workers "{boltz_params['num_workers']}" \
            --step_scale "{boltz_params['step_scale']}" \
            --diffusion_samples "{boltz_params['diffusion_samples']}" \
            --recycling_steps "{boltz_params['recycling_steps']}" \
            --sampling_steps "{boltz_params['sampling_steps']}" \
            --output_format "{boltz_params['output_format']}" \
            --cache {boltz_cache_dir}
            print(f"Boltz2 prediction complete ({uniprot_ids.index(uid)+1}/{len(uniprot_ids)}): {boltz_out_dir}")

        boltz_output_pdb_file = get_boltz_output_pdb(molecule_name)

        if not boltz_output_pdb_file:
            print(f"Skipping {uid} due to missing Boltz2 output PDB")
            continue

        # Run ESM2 analysis

        print(f"Running ESM2 analysis {uid} ({uniprot_ids.index(uid)+1}/{len(uniprot_ids)})")
        functional_anchors, flexible_anchors = predict_anchors_from_boltz2(
        pdb_file=boltz_output_pdb_file,
        model=model,
        batch_converter=batch_converter,
        functional_percentile=functional_percentile,
        flexible_percentile=flexible_percentile
        )

        functional_sites = [i for i, _ in functional_anchors]
        flexible_sites = [i for i, _ in flexible_anchors]
        esm_annotations = {"functional_sites": functional_sites, "flexible_sites": flexible_sites}

        if not esm_annotations:
            print(f"Skipping {uid} due to missing ESM annotations")
            continue

        # Refine structure
        refined_pdb = refine_with_esm(
            pred_pdb=boltz_output_pdb_file,
            esm_annotations=esm_annotations,
            out_dir=refine_out_dir,
            move_factor=0.2
        )

        # Download ground truth and calculate RMSD
        ref_pdb = download_pdb_from_uniprot(uid)
        
        if not ref_pdb:
            print(f"Skipping {uid} due to missing reference PDB")
            continue

        if ref_pdb:
            rmsd_boltz = calc_rmsd(boltz_output_pdb_file, ref_pdb)
            rmsd_refined = calc_rmsd(refined_pdb, ref_pdb)
            improvement = rmsd_boltz - rmsd_refined if rmsd_boltz and rmsd_refined else None

            print(f"{uid} RMSD: Boltz2={rmsd_boltz:.3f}, Refined={rmsd_refined:.3f}, Improvement={improvement:.3f}")

            # Store results
            rmsd_results.append({
            "uniprot_id": uid,
            "boltz2_rmsd": rmsd_boltz,
            "refined_rmsd": rmsd_refined,
            "improvement": rmsd_boltz - rmsd_refined,
            "percentage_improvement": ((rmsd_boltz - rmsd_refined) / rmsd_boltz * 100) if rmsd_boltz else 0.0,
            
            # Boltz2 parameters
            "boltz_model": boltz_params["model_name"],
            "boltz_devices": boltz_params["devices"],
            "boltz_accelerator": boltz_params["accelerator"],
            "boltz_use_potentials": boltz_params["use_potentials"],
            "boltz_num_workers": boltz_params["num_workers"],
            "boltz_step_scale": boltz_params["step_scale"],
            "boltz_diffusion_samples": boltz_params["diffusion_samples"],
            "boltz_recycling_steps": boltz_params["recycling_steps"],
            "boltz_sampling_steps": boltz_params["sampling_steps"],
            #"boltz_output_format": boltz_params["output_format"],

            # ESM parameters
            "esm_model": esm_model_name,
            "functional_percentile": functional_percentile,
            "flexible_percentile": flexible_percentile,

            # Refinement parameter
            "move_factor": move_factor
        })

 #Create df
rmsd_df = pd.DataFrame(rmsd_results)

# Compute averages
avg_boltz = rmsd_df['boltz2_rmsd'].mean()
avg_refined = rmsd_df['refined_rmsd'].mean()
avg_improvement = rmsd_df['improvement'].mean()
avg_percentage = ((rmsd_df['boltz2_rmsd'] - rmsd_df['refined_rmsd']) / rmsd_df['boltz2_rmsd'] * 100).mean()

# Add a final row
avg_row = {
    "uniprot_id": "AVERAGE",
    "boltz2_rmsd": avg_boltz,
    "refined_rmsd": avg_refined,
    "improvement": avg_improvement,
    "percentage_improvement": avg_percentage,
}

# Save to CSV

rmsd_csv_path = "./rmsd_results.csv"
rmsd_df = pd.concat([rmsd_df, pd.DataFrame([avg_row])], ignore_index=True)

rmsd_df.to_csv(rmsd_csv_path, index=False)
print(f"RMSD results saved to {rmsd_csv_path}")
print("Average RMSD Improvement Percentage: "f"{avg_percentage:.2f}%")

Loading ESM model: esm2_t33_650M_UR50D
Attempting to fetch P01033
Single YAML created: c:\School\URECA\Code\RefinementExperiment\yamls\P01033.yaml
Found Boltz2 output PDB for P01033, skipping Boltz2 prediction
Running ESM2 analysis P01033 (1/1)
Extracted sequence from PDB (length=207)
Predicted 20 functional anchors and 42 flexible regions
Downloaded PDB for P01033: ./ground_truth\P01033_1d2b.pdb
P01033 RMSD: Boltz2=14.823, Refined=13.662, Improvement=1.161
RMSD results saved to ./rmsd_results.csv
Average RMSD Improvement Percentage: 7.83%


In [ ]:
rmsd_df

uniprot_id  boltz2_rmsd  refined_rmsd  improvement  percentage_improvement  \
0      P69905    14.768460     13.629772     1.138689                7.710273   
1      P02144    15.503038     14.372207     1.130832                7.294260   
2      P61626    15.411616     14.007861     1.403755                9.108421   
3      P42212    16.272847     15.192559     1.080287                6.638589   
4      P02769    14.699916     14.193492     0.506424                3.445081   
5      P02763    18.308306     16.988969     1.319337                7.206220   
6      P02760    16.678126     15.606327     1.071799                6.426376   
7      P02748    43.053984     42.983952     0.070032                0.162662   
8      P02747    19.035458     17.876407     1.159051                6.088906   
9      P02750    23.758607     23.156270     0.602338                2.535240   
10     P02752    17.398457     16.378210     1.020247                5.864009   
11     P02753    16.998834     15.693601     1.305233                7.678366   
12     P02754    15.486001     14.106165     1.379836                8.910215   
13    AVERAGE    19.028742     18.014292     1.014451                6.082201   

   boltz_model  boltz_devices boltz_accelerator boltz_use_potentials  \
0       boltz2            1.0               gpu                 True   
1       boltz2            1.0               gpu                 True   
2       boltz2            1.0               gpu                 True   
3       boltz2            1.0               gpu                 True   
4       boltz2            1.0               gpu                 True   
5       boltz2            1.0               gpu                 True   
6       boltz2            1.0               gpu                 True   
7       boltz2            1.0               gpu                 True   
8       boltz2            1.0               gpu                 True   
9       boltz2            1.0               gpu                 True   
10      boltz2            1.0               gpu                 True   
11      boltz2            1.0               gpu                 True   
12      boltz2            1.0               gpu                 True   
13         NaN            NaN               NaN                  NaN   

    boltz_num_workers  boltz_step_scale  boltz_diffusion_samples  \
0                 8.0             1.638                      1.0   
1                 8.0             1.638                      1.0   
2                 8.0             1.638                      1.0   
3                 8.0             1.638                      1.0   
4                 8.0             1.638                      1.0   
5                 8.0             1.638                      1.0   
6                 8.0             1.638                      1.0   
7                 8.0             1.638                      1.0   
8                 8.0             1.638                      1.0   
9                 8.0             1.638                      1.0   
10                8.0             1.638                      1.0   
11                8.0             1.638                      1.0   
12                8.0             1.638                      1.0   
13                NaN               NaN                      NaN   

    boltz_recycling_steps  boltz_sampling_steps            esm_model  \
0                     3.0                  50.0  esm2_t33_650M_UR50D   
1                     3.0                  50.0  esm2_t33_650M_UR50D   
2                     3.0                  50.0  esm2_t33_650M_UR50D   
3                     3.0                  50.0  esm2_t33_650M_UR50D   
4                     3.0                  50.0  esm2_t33_650M_UR50D   
5                     3.0                  50.0  esm2_t33_650M_UR50D   
6                     3.0                  50.0  esm2_t33_650M_UR50D   
7                     3.0                  50.0  esm2_t33_650M_UR50D   
8                     3.0            

In [ ]:
#Display 3D structures
import py3Dmol

# Directory containing refined PDBs
pdb_files = [f for f in os.listdir(refine_out_dir) if f.endswith(".pdb")]

# Display all PDBs
for pdb_file in pdb_files:
    pdb_path = os.path.join(refine_out_dir, pdb_file)
    with open(pdb_path, "r") as f:
        pdb_data = f.read()
    
    print(f"Displaying: {pdb_file}")
    view = py3Dmol.view(width=600, height=400)
    view.addModel(pdb_data, "pdb")
    view.setStyle({'cartoon': {'color':'spectrum'}})
    view.setBackgroundColor('0xeeeeee')
    view.zoomTo()
    view.show()


Displaying: P02144_model_0_refined.pdb


3Dmol.js failed to load for some reason. Please check your browser console for error messages.

Displaying: P02742_model_0_refined.pdb


3Dmol.js failed to load for some reason. Please check your browser console for error messages.

Displaying: P02747_model_0_refined.pdb


...

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

Displaying: P61626_model_0_refined.pdb


3Dmol.js failed to load for some reason. Please check your browser console for error messages.

Displaying: P69905_model_0_refined.pdb


3Dmol.js failed to load for some reason. Please check your browser console for error messages.